In [26]:
# Block 1: Importing Libraries
import tarfile
import resampy
import pandas as pd
import librosa
import numpy as np
import os
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout
from tensorflow.keras.optimizers import Adam

In [27]:
# Block 2: Extracting Data
# Extract train_mp3s.tar
with tarfile.open('train_mp3s.tar', 'r') as tar:
    tar.extractall('train_mp3s')

# Extract test_mp3s.tar
with tarfile.open('test_mp3s.tar', 'r') as tar:
    tar.extractall('test_mp3s')

train_labels = np.loadtxt('train_label.txt', dtype=int)


In [28]:
# Block 3: Preprocessing Functions
import resampy
def preprocess_audio(file_path):
    try:
        audio, sample_rate = librosa.load(file_path, res_type='kaiser_fast')
        print(f"Loaded audio file: {file_path}")
        mfccs = librosa.feature.mfcc(y=audio, sr=sample_rate, n_mfcc=40)
        mfccs_scaled = np.mean(mfccs.T, axis=0)
        print(f"Extracted MFCCs: {mfccs_scaled.shape}")
        return mfccs_scaled
    except Exception as e:
        print(f"Error processing file: {file_path}")
        print(f"Error message: {str(e)}")
        return None

def prepare_data(directory):
    features = []
    for i in range(len(os.listdir(directory))):
        file_name = f"{i}.mp3"
        file_path = os.path.join(directory, file_name)
        print(f"Processing file: {file_path}")
        mfccs = preprocess_audio(file_path)
        if mfccs is not None:
            features.append(mfccs)
    print(f"Processed {len(features)} audio files")
    return np.array(features)

In [29]:
# Block 4: Preparing Data
train_features = prepare_data('train_mp3s/train_mp3s')
print(f"Train features shape: {train_features.shape}")

test_features = prepare_data('test_mp3s/test_mp3s')
print(f"Test features shape: {test_features.shape}")

train_labels = np.array([int(label) for label in train_labels])
print(f"Train labels shape: {train_labels.shape}")

print(f"Number of training features: {len(train_features)}")
print(f"Number of training labels: {len(train_labels)}")
print(f"Number of test features: {len(test_features)}")

if len(train_features) == 0:
    print("No training features available. Please check the data.")

Processing file: train_mp3s/train_mp3s\0.mp3
Loaded audio file: train_mp3s/train_mp3s\0.mp3
Extracted MFCCs: (40,)
Processing file: train_mp3s/train_mp3s\1.mp3
Loaded audio file: train_mp3s/train_mp3s\1.mp3
Extracted MFCCs: (40,)
Processing file: train_mp3s/train_mp3s\2.mp3
Loaded audio file: train_mp3s/train_mp3s\2.mp3
Extracted MFCCs: (40,)
Processing file: train_mp3s/train_mp3s\3.mp3
Loaded audio file: train_mp3s/train_mp3s\3.mp3
Extracted MFCCs: (40,)
Processing file: train_mp3s/train_mp3s\4.mp3
Loaded audio file: train_mp3s/train_mp3s\4.mp3
Extracted MFCCs: (40,)
Processing file: train_mp3s/train_mp3s\5.mp3
Loaded audio file: train_mp3s/train_mp3s\5.mp3
Extracted MFCCs: (40,)
Processing file: train_mp3s/train_mp3s\6.mp3
Loaded audio file: train_mp3s/train_mp3s\6.mp3
Extracted MFCCs: (40,)
Processing file: train_mp3s/train_mp3s\7.mp3
Loaded audio file: train_mp3s/train_mp3s\7.mp3
Extracted MFCCs: (40,)
Processing file: train_mp3s/train_mp3s\8.mp3
Loaded audio file: train_mp3s/train

C:\Users\mojii\AppData\Local\Temp\ipykernel_18928\434947731.py:5: UserWarning: PySoundFile failed. Trying audioread instead.
  audio, sample_rate = librosa.load(file_path, res_type='kaiser_fast')


Error processing file: train_mp3s/train_mp3s\14173.mp3
Error message: [Errno 2] No such file or directory: 'train_mp3s/train_mp3s\\14173.mp3'
Processing file: train_mp3s/train_mp3s\14174.mp3
Error processing file: train_mp3s/train_mp3s\14174.mp3
Error message: [Errno 2] No such file or directory: 'train_mp3s/train_mp3s\\14174.mp3'
Processing file: train_mp3s/train_mp3s\14175.mp3
Error processing file: train_mp3s/train_mp3s\14175.mp3
Error message: [Errno 2] No such file or directory: 'train_mp3s/train_mp3s\\14175.mp3'
Processing file: train_mp3s/train_mp3s\14176.mp3
Error processing file: train_mp3s/train_mp3s\14176.mp3
Error message: [Errno 2] No such file or directory: 'train_mp3s/train_mp3s\\14176.mp3'
Processing file: train_mp3s/train_mp3s\14177.mp3
Error processing file: train_mp3s/train_mp3s\14177.mp3
Error message: [Errno 2] No such file or directory: 'train_mp3s/train_mp3s\\14177.mp3'
Processing file: train_mp3s/train_mp3s\14178.mp3
Error processing file: train_mp3s/train_mp3s\

In [30]:
# Block 5: Model Training and Prediction
if len(train_features) > 0:
    train_data, val_data, train_labels, val_labels = train_test_split(train_features, train_labels, test_size=0.3, random_state=42)
    
    model = Sequential([
        Dense(128, activation='relu', input_shape=(40,)),
        Dropout(0.5),
        Dense(64, activation='relu'),
        Dropout(0.5),
        Dense(4, activation='softmax')
    ])
    
    model.compile(optimizer=Adam(learning_rate=0.001),
                  loss='sparse_categorical_crossentropy',
                  metrics=['accuracy'])
    
    model.fit(train_data, train_labels, validation_data=(val_data, val_labels), epochs=50, batch_size=32)
    
    predictions = model.predict(test_features)
    predicted_labels = np.argmax(predictions, axis=1)
    
    submission = pd.DataFrame({'id': range(len(predicted_labels)), 'category': predicted_labels})
    submission.to_csv('submission.csv', index=False)
else:
    print("No training features available. Please check the data.")

Epoch 1/50
260/260 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step - accuracy: 0.3276 - loss: 11.5170 - val_accuracy: 0.3716 - val_loss: 1.3247
Epoch 2/50
260/260 ━━━━━━━━━━━━━━━━━━━━ 0s 931us/step - accuracy: 0.3548 - loss: 1.4691 - val_accuracy: 0.3704 - val_loss: 1.2568
Epoch 3/50
260/260 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.3672 - loss: 1.3006 - val_accuracy: 0.4358 - val_loss: 1.1811
Epoch 4/50
260/260 ━━━━━━━━━━━━━━━━━━━━ 0s 987us/step - accuracy: 0.4180 - loss: 1.2601 - val_accuracy: 0.5244 - val_loss: 1.1637
Epoch 5/50
260/260 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.4458 - loss: 1.2166 - val_accuracy: 0.5670 - val_loss: 1.0898
Epoch 6/50
260/260 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.4617 - loss: 1.1747 - val_accuracy: 0.5709 - val_loss: 1.0625
Epoch 7/50
260/260 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.4939 - loss: 1.1306 - val_accuracy: 0.5847 - val_loss: 1.0174
Epoch 8/50
260/260 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.5169 - loss: 1.0968 - val_accurac